In [1]:
import numpy as np
import matplotlib.pyplot as plt
%config InlineBackend.figure_format = 'retina'
%matplotlib osx
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import matplotlib.pyplot as plt

In [2]:
# Adjustment for boundary conditions

def adjust_x(x):
    if x > 180:
        x = x - 360
    elif x < -180:
        x = x + 360

    return x

def adjust_y(y):
    if y > 90:
        y = 90
    elif y < -90:
        y = -90

    return y


In [3]:
# Velocity functions

# Define 4 basic velocities depending on latitude
def get_base_velocity(y):

    if (y >= 45) and (y < 90):
        bx = 10
        by = 3

    elif (y >= 0) and (y < 45):
        bx = 5
        by = 3
        
    elif (y >= -45) and (y < 0):
        bx = 5
        by = 3
        
    elif (y >= -90) and (y < -45):
        bx = 10
        by = 3
        
    else:
        bx = 1
        by = 1

    # multiply velocity by dt to get dx to add to previous particle position when updating position
    # dt = 0.8
    if (t < 2) and (i < 2):
        dt = 0.3
    else:
        dt = 1

    return bx*dt, by*dt


# Apply randomness to the base velocity for the simulation
# Without this randonmness there are somewhat regularly-spaced particles
def get_abs_velocity(y):
    bx, by = get_base_velocity(y)
    
    ax = np.random.random() * bx
    ay = np.random.random() * by
    
    return ax, ay
    
    
# Random particle direction chosen with a certain probability
def random_sign(prob):
    if np.random.random() <= prob:
        return +1
    else:
        return -1


# Apply this random direction to the absolute velocity depending on
# the expected movement as a function of latitude
# This is the core of the simulation
def get_velocity(y):
    ax, ay = get_abs_velocity(y)
    
    if y >= 0:  # Northern Hemisphere
        
        if y <= 15:
            vx = - random_sign(.7) * ax  # preference to go west
            vy = - random_sign(.6) * ay  # some preference to go south

        elif y <= 30:
            vx = - random_sign(.6) * ax  # some preference to go west
            vy = - random_sign(.5) * ay  # some preference to go south

        elif y <= 45:
            vx = + random_sign(.8) * ax  # some preference to go east
            vy = + random_sign(.50) * ay ###

        elif y <= 60:
            vx = + random_sign(.7) * ax  # some preference to go east
            vy = + random_sign(.55) * ay

        else:
            vx = + random_sign(.6) * ax  # some preference to go east
            vy = + random_sign(.50) * ay  # 

    else:  # Southern Hemisphere
        
        if y >= -15:
            vx = - random_sign(.7) * ax  # some preference to go west
            vy = - random_sign(.51) * ay  # some preference to go south

        elif y >= -30:
            vx = - random_sign(.6) * ax  # some preference to go west
            vy = - random_sign(.6) * ay

        elif y >= -60:
            vx = + random_sign(.7) * ax  # some preference to go east
            vy = - random_sign(.55) * ay

        else:
            vx = - random_sign(.7) * ax  # some preference to go west
            vy = - random_sign(.6) * ay
        
    return vx, vy


In [4]:
# Update the position by just adding the (velocity * delta time) result calculated from previous functions
def update_position(x, y):
    dx, dy = get_velocity(y)
    
    x = x + dx
    y = y + dy

    return adjust_x(x), adjust_y(y)


In [5]:
# N-particle simulation

# Define Emission Source Points:
initial_points = [
    (-83.060926, 42.136168),
    (-120.060926, 34.),
    (0, 37.),
]

# Number of Particles per source
N_per_source = 1000 
    
# Initialize array with the particles for each source
position_array = []
for p in initial_points:
    position_array += [p for n in range(N_per_source)]

# Number of position changes per overarching time step
nn = 15


from matplotlib.animation import FFMpegWriter
metadata = dict(title='animationf', artist='Paula',comment='Project')
writer = FFMpegWriter(fps=6, metadata=metadata,bitrate=200000)
fig = plt.figure(figsize=(18,10))

with writer.saving(fig, "animationf.mp4", dpi=200):
    total_time = 28
    time = np.arange(0, total_time, 2)
    for t in time:
        if t < 12:
            for i in range(nn):

                fig.clear()

                N = len(position_array)

                for n in range(N):
                    x, y = position_array[n]
                    x, y = update_position(x,y)
                    position_array[n] = [x, y]

                xs = [x for (x, y) in position_array]
                ys = [y for (x, y) in position_array]

                ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree(central_longitude = 0)) #PlateCarree
                ax.coastlines(resolution='110m', color='gray')
                ax.gridlines()

                ax.set_extent(
                    [
                        -180, 
                        180,
                        -90, 
                        90 
                    ],
                    crs=ccrs.PlateCarree()
                )

                ms = 2 # marker size

                plt.plot(xs, ys, 'o', markersize=ms, color="purple", alpha = 0.5)

                equatorx = np.arange(-180, 180, 1)
                equatory = np.full(360,0)

                plt.plot(equatorx, equatory, 'k--')
                plt.title('Simulating Atmospheric Transport of Carbon Dioxide Emissions \n Time = {:.2f} years'.format(t/12), c='blue', fontsize=18)
                plt.xticks([ -180, -120, -60, 0, 60, 120, 180])
                plt.yticks([ -90, -60, -30, 0, 30, 60, 90])
                plt.xlim([-180, 180])
                plt.ylim([-90, 90])
                plt.xlabel('Longitude', fontsize=15)
                plt.ylabel('Latitude', fontsize=15)
                plt.draw()
                plt.pause(0.01)
                writer.grab_frame()

        if t >= 12:
            for i in range(nn):
                fig.clear()

                for n in range(N):
                    x, y = position_array[n]
                    x, y = update_position(x,y)
                    position_array[n] = [x, y]

                xs = [x for (x, y) in position_array]
                ys = [y for (x, y) in position_array]
                ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree(central_longitude = 0)) #PlateCarree
                ax.coastlines(resolution='110m', color='gray')
                ax.gridlines()

                ax.set_extent(
                    [
                        -180, 
                        180, 
                        -90, 
                        90 
                    ],
                    crs=ccrs.PlateCarree()
                )

                ms = 2 # marker size
                ys = np.array(ys)
                xs = np.array(xs)

                y_NH = ys[ys>=0]
                x_NH = xs[ys>=0]

                y_SH = ys[ys<0]
                x_SH = xs[ys<0]

                plt.plot(x_NH, y_NH, 'o', markersize=ms, color="purple", alpha = 0.5)
                plt.plot(x_SH, y_SH, 'o', markersize=ms, color="purple", alpha = 0.5)

                equatorx = np.arange(-180, 180, 1)
                equatory = np.full(360,0)

                plt.plot(equatorx, equatory, 'k--')

                plt.title('Simulating Atmospheric Transport of Carbon Dioxide Emissions \n Time = {:.2f} years'.format(t/12), c='red', fontsize=18)
                plt.xticks([ -180, -120, -60, 0, 60, 120, 180])
                plt.yticks([ -90, -60, -30, 0, 30, 60, 90])
                plt.xlim([-180, 180])
                plt.ylim([-90, 90])
                plt.xlabel('Longitude', fontsize=15)
                plt.ylabel('Latitude', fontsize=15)
                plt.draw()
                plt.pause(0.01) 
                writer.grab_frame()

    plt.show()

In [6]:
t

26